In [1]:
import numpy as np
import keras
import os
from pathlib import Path
import requests
import zipfile

### Download the data

In [2]:
url = "https://www.manythings.org/anki/pol-eng.zip"
local_filename = url.split('/')[-1]
dirpath = Path().absolute()

headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'
}

response = requests.get(url, headers=headers)
if response.status_code == 200:
    with open(local_filename, 'wb') as f:
        f.write(response.content)
    with zipfile.ZipFile(local_filename, 'r') as zip_ref:
        zip_ref.extractall(dirpath)

### Configuration

In [3]:
batch_size = 64  # Batch size for training.
epochs = 200  # Number of epochs to train for.
latent_dim = 256  # Latent dimensionality of the encoding space.
num_samples = 10000  # Number of samples to train on.
# Path to the data txt file on disk.
data_path = os.path.join(dirpath, "pol.txt")

### Prepare the data

In [4]:
# Vectorize the data.
input_texts = []
target_texts = []
input_characters = set()
target_characters = set()
with open(data_path, "r", encoding="utf-8") as f:
    lines = f.read().split("\n")
for line in lines[: min(num_samples, len(lines) - 1)]:
    input_text, target_text, _ = line.split("\t")
    # We use "tab" as the "start sequence" character
    # for the targets, and "\n" as "end sequence" character.
    target_text = "\t" + target_text + "\n"
    input_texts.append(input_text)
    target_texts.append(target_text)
    for char in input_text:
        if char not in input_characters:
            input_characters.add(char)
    for char in target_text:
        if char not in target_characters:
            target_characters.add(char)

input_characters = sorted(list(input_characters))
target_characters = sorted(list(target_characters))
num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)
max_encoder_seq_length = max([len(txt) for txt in input_texts])
max_decoder_seq_length = max([len(txt) for txt in target_texts])

print("Number of samples:", len(input_texts))
print("Number of unique input tokens:", num_encoder_tokens)
print("Number of unique output tokens:", num_decoder_tokens)
print("Max sequence length for inputs:", max_encoder_seq_length)
print("Max sequence length for outputs:", max_decoder_seq_length)

input_token_index = dict([(char, i) for i, char in enumerate(input_characters)])
target_token_index = dict([(char, i) for i, char in enumerate(target_characters)])

encoder_input_data = np.zeros(
    (len(input_texts), max_encoder_seq_length, num_encoder_tokens),
    dtype="float32",
)
decoder_input_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)
decoder_target_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)

for i, (input_text, target_text) in enumerate(zip(input_texts, target_texts)):
    for t, char in enumerate(input_text):
        encoder_input_data[i, t, input_token_index[char]] = 1.0
    encoder_input_data[i, t + 1 :, input_token_index[" "]] = 1.0
    for t, char in enumerate(target_text):
        # decoder_target_data is ahead of decoder_input_data by one timestep
        decoder_input_data[i, t, target_token_index[char]] = 1.0
        if t > 0:
            # decoder_target_data will be ahead by one timestep
            # and will not include the start character.
            decoder_target_data[i, t - 1, target_token_index[char]] = 1.0
    decoder_input_data[i, t + 1 :, target_token_index[" "]] = 1.0
    decoder_target_data[i, t:, target_token_index[" "]] = 1.0

Number of samples: 10000
Number of unique input tokens: 70
Number of unique output tokens: 87
Max sequence length for inputs: 19
Max sequence length for outputs: 52


### Build the model

In [5]:
# Define an input sequence and process it.
encoder_inputs = keras.Input(shape=(None, num_encoder_tokens))
encoder = keras.layers.LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)

# We discard `encoder_outputs` and only keep the states.
encoder_states = [state_h, state_c]

# Set up the decoder, using `encoder_states` as initial state.
decoder_inputs = keras.Input(shape=(None, num_decoder_tokens))

# We set up our decoder to return full output sequences,
# and to return internal states as well. We don't use the
# return states in the training model, but we will use them in inference.
decoder_lstm = keras.layers.LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=encoder_states)
decoder_dense = keras.layers.Dense(num_decoder_tokens, activation="softmax")
decoder_outputs = decoder_dense(decoder_outputs)

# Define the model that will turn
# `encoder_input_data` & `decoder_input_data` into `decoder_target_data`
model = keras.Model([encoder_inputs, decoder_inputs], decoder_outputs)

### Train the model

In [6]:
model.compile(
    optimizer="rmsprop", loss="categorical_crossentropy", metrics=["accuracy"]
)
model.fit(
    [encoder_input_data, decoder_input_data],
    decoder_target_data,
    batch_size=batch_size,
    epochs=epochs,
    validation_split=0.2,
)

model.save("s2s_model.keras")


Epoch 1/200


125/125 [==============================] - 20s 121ms/step - loss: 1.3745 - accuracy: 0.6987 - val_loss: 1.4872 - val_accuracy: 0.6530
Epoch 2/200
125/125 [==============================] - 12s 94ms/step - loss: 1.0822 - accuracy: 0.7185 - val_loss: 1.2406 - val_accuracy: 0.6688
Epoch 3/200
125/125 [==============================] - 14s 109ms/step - loss: 0.9703 - accuracy: 0.7424 - val_loss: 1.1089 - val_accuracy: 0.7065
Epoch 4/200
125/125 [==============================] - 14s 109ms/step - loss: 0.8733 - accuracy: 0.7671 - val_loss: 1.0149 - val_accuracy: 0.7165
Epoch 5/200
125/125 [==============================] - 18s 145ms/step - loss: 0.7839 - accuracy: 0.7835 - val_loss: 0.9353 - val_accuracy: 0.7399
Epoch 6/200
125/125 [==============================] - 16s 129ms/step - loss: 0.7367 - accuracy: 0.7946 - val_loss: 0.8968 - val_accuracy: 0.7464
Epoch 7/200
125/125 [==============================] - 15s 121ms/step - loss: 0.7030 - accuracy: 0.8006 - val_loss: 0.8677

125/125 [==============================] - 15s 122ms/step - loss: 0.3459 - accuracy: 0.9002 - val_loss: 0.6133 - val_accuracy: 0.8282
Epoch 53/200
125/125 [==============================] - 14s 115ms/step - loss: 0.3415 - accuracy: 0.9015 - val_loss: 0.6171 - val_accuracy: 0.8282
Epoch 54/200
125/125 [==============================] - 15s 119ms/step - loss: 0.3375 - accuracy: 0.9020 - val_loss: 0.6109 - val_accuracy: 0.8300
Epoch 55/200
125/125 [==============================] - 18s 143ms/step - loss: 0.3326 - accuracy: 0.9039 - val_loss: 0.6103 - val_accuracy: 0.8302
Epoch 56/200
125/125 [==============================] - 16s 130ms/step - loss: 0.3283 - accuracy: 0.9047 - val_loss: 0.6132 - val_accuracy: 0.8305
Epoch 57/200
125/125 [==============================] - 16s 132ms/step - loss: 0.3243 - accuracy: 0.9062 - val_loss: 0.6136 - val_accuracy: 0.8303
Epoch 58/200
125/125 [==============================] - 15s 122ms/step - loss: 0.3195 - accuracy: 0.9077 - val_loss: 0.6206 - val_a

Epoch 108/200
125/125 [==============================] - 18s 145ms/step - loss: 0.1583 - accuracy: 0.9548 - val_loss: 0.7820 - val_accuracy: 0.8268
Epoch 109/200
125/125 [==============================] - 18s 143ms/step - loss: 0.1564 - accuracy: 0.9550 - val_loss: 0.7863 - val_accuracy: 0.8266
Epoch 110/200
125/125 [==============================] - 19s 149ms/step - loss: 0.1544 - accuracy: 0.9558 - val_loss: 0.7927 - val_accuracy: 0.8259
Epoch 111/200
125/125 [==============================] - 18s 146ms/step - loss: 0.1517 - accuracy: 0.9566 - val_loss: 0.7972 - val_accuracy: 0.8257
Epoch 112/200
125/125 [==============================] - 19s 150ms/step - loss: 0.1490 - accuracy: 0.9573 - val_loss: 0.8031 - val_accuracy: 0.8262
Epoch 113/200
125/125 [==============================] - 21s 172ms/step - loss: 0.1478 - accuracy: 0.9575 - val_loss: 0.8029 - val_accuracy: 0.8261
Epoch 114/200
125/125 [==============================] - 27s 215ms/step - loss: 0.1459 - accuracy: 0.9580 - val_

125/125 [==============================] - 12s 98ms/step - loss: 0.0751 - accuracy: 0.9787 - val_loss: 1.0155 - val_accuracy: 0.8201
Epoch 164/200
125/125 [==============================] - 12s 97ms/step - loss: 0.0749 - accuracy: 0.9786 - val_loss: 1.0207 - val_accuracy: 0.8214
Epoch 165/200
125/125 [==============================] - 13s 100ms/step - loss: 0.0734 - accuracy: 0.9792 - val_loss: 1.0302 - val_accuracy: 0.8214
Epoch 166/200
125/125 [==============================] - 13s 103ms/step - loss: 0.0725 - accuracy: 0.9796 - val_loss: 1.0320 - val_accuracy: 0.8208
Epoch 167/200
125/125 [==============================] - 12s 99ms/step - loss: 0.0716 - accuracy: 0.9797 - val_loss: 1.0349 - val_accuracy: 0.8209
Epoch 168/200
125/125 [==============================] - 13s 101ms/step - loss: 0.0706 - accuracy: 0.9799 - val_loss: 1.0365 - val_accuracy: 0.8204
Epoch 169/200
125/125 [==============================] - 12s 100ms/step - loss: 0.0694 - accuracy: 0.9803 - val_loss: 1.0432 - va

### Run interference

In [7]:
encoder_inputs = model.input[0]  # input_1
encoder_outputs, state_h_enc, state_c_enc = model.layers[2].output  # lstm_1
encoder_states = [state_h_enc, state_c_enc]
encoder_model = keras.Model(encoder_inputs, encoder_states)

decoder_inputs = model.input[1]  # input_2
decoder_state_input_h = keras.Input(shape=(latent_dim,))
decoder_state_input_c = keras.Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
decoder_lstm = model.layers[3]
decoder_outputs, state_h_dec, state_c_dec = decoder_lstm(
    decoder_inputs, initial_state=decoder_states_inputs
)
decoder_states = [state_h_dec, state_c_dec]
decoder_dense = model.layers[4]
decoder_outputs = decoder_dense(decoder_outputs)
decoder_model = keras.Model(
    [decoder_inputs] + decoder_states_inputs, [decoder_outputs] + decoder_states
)

# Reverse-lookup token index to decode sequences back to
# something readable.
reverse_input_char_index = dict((i, char) for char, i in input_token_index.items())
reverse_target_char_index = dict((i, char) for char, i in target_token_index.items())


def decode_sequence(input_seq):
    # Encode the input as state vectors.
    states_value = encoder_model.predict(input_seq, verbose=0)

    # Generate empty target sequence of length 1.
    target_seq = np.zeros((1, 1, num_decoder_tokens))
    # Populate the first character of target sequence with the start character.
    target_seq[0, 0, target_token_index["\t"]] = 1.0

    # Sampling loop for a batch of sequences
    # (to simplify, here we assume a batch of size 1).
    stop_condition = False
    decoded_sentence = ""
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict(
            [target_seq] + states_value, verbose=0
        )

        # Sample a token
        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += sampled_char

        # Exit condition: either hit max length
        # or find stop character.
        if sampled_char == "\n" or len(decoded_sentence) > max_decoder_seq_length:
            stop_condition = True

        # Update the target sequence (of length 1).
        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.0

        # Update states
        states_value = [h, c]
    return decoded_sentence

In [8]:
for seq_index in range(20):
    # Take one sequence (part of the training set)
    # for trying out decoding.
    input_seq = encoder_input_data[seq_index : seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    print("-")
    print("Input sentence:", input_texts[seq_index])
    print("Decoded sentence:", decoded_sentence)

-
Input sentence: Go.
Decoded sentence: Idź.

-
Input sentence: Hi.
Decoded sentence: Cześć.

-
Input sentence: Run!
Decoded sentence: Uciekaj!

-
Input sentence: Run.
Decoded sentence: Uciekaj.

-
Input sentence: Run.
Decoded sentence: Uciekaj.

-
Input sentence: Who?
Decoded sentence: Kto?

-
Input sentence: Wow!
Decoded sentence: O, dziama?

-
Input sentence: Wow!
Decoded sentence: O, dziama?

-
Input sentence: Duck!
Decoded sentence: Unik!

-
Input sentence: Fire!
Decoded sentence: Strzelaj!

-
Input sentence: Fire!
Decoded sentence: Strzelaj!

-
Input sentence: Fire!
Decoded sentence: Strzelaj!

-
Input sentence: Help!
Decoded sentence: Pomocy!

-
Input sentence: Hide.
Decoded sentence: Schowaj się.

-
Input sentence: Jump!
Decoded sentence: Skacz!

-
Input sentence: Jump.
Decoded sentence: Skok.

-
Input sentence: Stay.
Decoded sentence: Zostań.

-
Input sentence: Stop!
Decoded sentence: Zatrzymaj się!

-
Input sentence: Stop!
Decoded sentence: Zatrzymaj się!

-
Input sentence: W

### Bleu evaluation

In [9]:
import nltk.translate.bleu_score as bleu
smoothing_function = bleu.SmoothingFunction().method4
bleu_scores = 0
for seq_index in range(len(encoder_input_data)):
    input_seq = encoder_input_data[seq_index : seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    reference = [list(target_texts[seq_index])]
    candidate = list(decoded_sentence.strip())
    bleu_score = bleu.sentence_bleu(reference, candidate, smoothing_function=smoothing_function)
    bleu_scores += bleu_score
    if seq_index % (len(encoder_input_data)//10) == 0 and seq_index != 0:
        print(bleu_scores/seq_index)
bleu_final = bleu_scores/len(encoder_input_data)
print("BLEU score:", bleu_final)

0.5965545320892247
0.5981615012338071
0.5930356751147987
0.5942200927187505
0.5951351487924014
0.5919465093543784
0.590832790904886
0.5919919489002385
0.5452219773056319
BLEU score: 0.5095920718253371
